In [1]:
using Pkg; Pkg.activate(@__DIR__); 

  Activating project at `~/Documents/eth_courses/notebooks/visualization/Lorenz-WebAssembly-Model.jl`


In [2]:
using OrdinaryDiffEq
using WGLMakie
using JSServe, Markdown
using StaticArrays
using StaticTools
using DiffEqGPU
import JSServe.TailwindDashboard as D
using FileIO

In [3]:
Page(exportable=true, offline=true) # for Franklin, you still need to configure
WGLMakie.activate!()
Makie.inline!(false) # Make sure to inline plots into Documenter output!

false

In [4]:
# must be true to be found inside the DOM
is_widget(x) = true
# Updating the widget isn't dependant on any other state (only thing supported right now)
is_independant(x) = true
# The values a widget can iterate
function value_range end
# updating the widget with a certain value (usually an observable)
function update_value!(x, value) end

update_value! (generic function with 1 method)

## Diffeq app

In [41]:
# forcing function
u(t) = 1

first_order_sys!(t,x;τ,u) = (u(t) - x) / τ

function first_order_sys!(X, params, t)
# function first_order_sys!(dX, X, params, t)

    # extract the parameters
    τ = params.τ

    # extract the state
    x = X[1]
    
    # x_dot = (u(t) - x) / τ
    x_dot = first_order_sys!(t,x;τ=τ,u=u)

    # dX[1] = x_dot
    return @SVector[x_dot]
end


first_order_sys! (generic function with 3 methods)

In [42]:

App() do session
    s = D.Slider("Time constant: ", 0.1:0.1:10.)

    # variables
    t = MallocVector{Float64}(undef,1000)
    y1 = MallocVector{Float64}(undef,1000)

    # diffeq solver
    X0 = @SVector [0.0]
    tspan = (0.0, 5.0)
    parameters = (;τ=0.2)
    
    prob2 = ODEProblem(first_order_sys!, X0, tspan, parameters)

    # plotting
    fig = Figure(resolution=(600,600))
    ax = Axis(fig[1, 1], limits=(tspan[1], tspan[2], 0, 1.))

    x_vec = Observable{Vector{Float64}}([0.])
    y_vec = Observable{Vector{Float64}}([0.])

    lines!(ax, x_vec, y_vec)

    # interactions
    app = map(s.widget.value) do val
        p2 = (;τ=Float64(val) / 10.0)
        
        integ2 = DiffEqGPU.init(GPUTsit5(), prob2.f, false, X0, 0.0, 0.005, p2, nothing, CallbackSet(nothing), true, false)

        for i in Int32(1):Int32(1000)
            t[i] = integ2.t
            y1[i] = integ2.u[1]
            
          @inline DiffEqGPU.step!(integ2, integ2.t + integ2.dt, integ2.u)
          
        end
        
        x_vec[] =  t
        y_vec[] =  y1
    end
    
    widget_box = D.FlexRow(D.FlexCol(s), D.Card(fig))
    
    return JSServe.record_states(session,   D.Card(widget_box) )
end

App(JSServe.var"#8#14"{var"#115#117"}(var"#115#117"()), Base.RefValue{Union{Nothing, Session}}(nothing), "JSServe App", false)

In [7]:
app = App() do session
    # slider = Slider(0.1:0.1:10)
    # menu = D.Dropdown( "",[sin, tan, cos])
    # cmap_button = D.Button("change colormap")
    # textfield = D.TextField("type in your text")

    # inp_1 = D.NumberInput(0.0)
    # inp_2 = D.NumberInput(0.0)
    # inp_3 = D.NumberInput(0.0)

    # cmap = map(cmap_button) do click
    # end

    # value = map(slider.value) do x
    #     # return x ^ 2
    # end

    # load mesh 
    crazyflie_stl = load(assetpath(String(@__DIR__) * "/assets/cf2_assembly.obj"))

    # show quad 
    fig = mesh(crazyflie_stl, figure = (resolution = (1800, 1000),))

    # slider_grid = DOM.div("z-index: ", slider, slider.value)
    
    # return JSServe.record_states(session, DOM.div(fig, slider_grid, menu, DOM.div("x: ",inp_1, "y: ",inp_2 , "z: ",inp_3)))
    return JSServe.record_states(session, DOM.div(fig))
end

App(JSServe.var"#8#14"{var"#21#22"}(var"#21#22"()), Base.RefValue{Union{Nothing, Session}}(nothing), "JSServe App", false)